In [5]:
from lxml import etree as ET
from pathlib import Path
import bs4
import re


def parse_xml(filename):
    root = ET.parse(filename)

    lines = []
    for paragraph in root.findall(".//{*}TextBlock"):
        for line in paragraph.findall('.//{*}TextLine'):
            textline = ""
            for string in line.findall(".//{*}String"):
                if 'SUBS_TYPE' in string.attrib:
                    if string.attrib['SUBS_TYPE'] == "HypPart1":
                        textline += string.attrib['SUBS_CONTENT'] + " "
                else:
                    textline += string.attrib['CONTENT'] + " "
            lines.append(textline[:-1])
    return lines

def parse_new_xml(filename):
    root = ET.parse(filename)

    lines = []
    for paragraph in root.findall(".//{*}textblock"):
        for line in paragraph.findall('.//{*}textline'):
            textline = ""
            for string in line.findall(".//{*}string"):
                if 'SUBS_TYPE' in string.attrib or "subs_type" in string.attrib:
                    print("parse_new_xml HEIHO", string.attrib)
                    if string.attrib['SUBS_TYPE'] == "HypPart1":
                        textline += string.attrib['SUBS_CONTENT'] + " "
                else:
                    textline += string.attrib['content'] + " "
            lines.append(textline[:-1])
    return lines

def parse_hocr(filename):
    lines=[]
    with open(filename, 'r') as data:
        txt = data.read()
        soup = bs4.BeautifulSoup(txt,'lxml')
        paras = soup.findAll("p", {"class": "ocr_par"})
        for para in paras:
            ocr_lines = para.findAll('span', {"class": "ocr_line"})
            for ocr_line in ocr_lines:
                line = ocr_line.text.replace("\n"," ").strip()
                lines.append(line)
            lines.append('')
    return lines


def get_book(bookdir):
    p = Path(bookdir)
    pages = ["\n".join(parse_xml(str(e))) for e in p.iterdir() if e.suffix == ".xml"]
    return pages

def get_new_book(bookdir):
    p = Path(bookdir)
    files = sorted([e for e in p.iterdir() if e.suffix == ".alto"])
    pages = ["\n".join(parse_new_xml(str(e))) for e in files]
    return pages

def get_hocr_book(bookdir):
    p = Path(bookdir)
    files = sorted([e for e in p.iterdir()])
    pages = ["\n".join(parse_hocr(str(f))) for f in files]
    return pages

In [6]:
from pathlib import Path

p = Path("reocr_batch_2/digibok/")

for x in p.iterdir():
    code = x.name.split("digibok_")[1]
    pages = get_hocr_book(x)
    text = "\n\n".join(pages)
    with open(f"nnn/{code}.txt", "w+") as f:
            f.write(text)

In [8]:
print(len(list(Path("nnn").iterdir())))

138


In [16]:
def get_code(filename):
    code = filename.split("digibok_")[1].split("_")[0]
    return code

p = Path("reocr_hocr_batch_2")
p1 = Path("dikt_split/bokmål/yes")
p2 = Path("dikt_split/nynorsk/yes")

codes1 = [f.name.split("-")[0] for f in p1.iterdir()] 
codes2 = [f.name.split("-")[0] for f in p2.iterdir()]

books = {}

for file in p.iterdir():
    code = get_code(file.name)

    page = "\n".join(parse_hocr(file))
    if code in books:
        books[code] += page
    else:
        books[code] = page

for code, book in books.items():
    if code in codes1:
        filename = p1 / f"{code}.txt"
    elif code in codes2:
        filename = p2 / f"{code}.txt"
    else:
        filename = p1 / f"{code}_w.txt"

    with filename.open("w+") as f:
        f.write(book)

In [21]:
import re

with open("dikt_split/bokmål/yes/2014102306006_w.txt") as f:
    content = f.read()

nums = re.findall(r"\d+\n", content)
strs = re.split(r"\d+\n", content)[:-1]
strnums = zip(nums, strs)
strnums = sorted(strnums, key= lambda x: x[0])
strnums

newcontent = "".join(s for n, s in strnums)

with open("dikt_split/bokmål/yes/2014102306006.txt", "w+") as f:
    f.write(newcontent)
    

In [19]:
print(books["2007062904043"])
for file in p.iterdir():
    code = get_code(file.name)
    if code == "2007062904043":
        text = file.read_text()
        print(text)


<?xml version="1.0" encoding="UTF-8"?>
<!DOCTYPE html PUBLIC "-//W3C//DTD XHTML 1.0 Transitional//EN"
    "http://www.w3.org/TR/xhtml1/DTD/xhtml1-transitional.dtd">
<html xmlns="http://www.w3.org/1999/xhtml" xml:lang="en" lang="en">
 <head>
  <title></title>
  <meta http-equiv="Content-Type" content="text/html;charset=utf-8"/>
  <meta name='ocr-system' content='tesseract 5.0.0' />
  <meta name='ocr-capabilities' content='ocr_page ocr_carea ocr_par ocr_line ocrx_word ocrp_wconf'/>
 </head>
 <body>
  <div class='ocr_page' id='page_1' title='image "/data/digibok_2007062904043_C1.tiff"; bbox 0 0 2247 3299; ppageno 0; scan_res 70 70'>
  </div>
 </body>
</html>



In [49]:
p1 = Path("dikt-ikke-idetfri/")
for x in p1.iterdir():
    if x.is_dir():
        pages = get_book(x)
        #print(x)
        #print("\n\n".join(pages))


In [58]:
p2 = Path("ny-ocr-dikt-idetfri/alto/")

for x in p2.iterdir():
    code = x.name.split("digibok_")[1]
    if x.is_dir():
        pages = get_new_book(x)
        text = "\n\n".join(pages)
        with open(f"ny-ocr-dikt-idetfri/{code}.txt", "w+") as f:
            f.write(text)


In [60]:
def get_code(filename):
    return filename.split("digibok_")[1].split("-")[0]

p_old = Path("dikt-idetfri/")
p_new = Path("ny-ocr-dikt-idetfri/")
#names_old_ocr = [e.name for e in p_old.iterdir() if e.suffix == ".txt"]
#codes_old_ocr = [get_code(name) for name in names]
codes_new_ocr = [e.name.split(".txt")[0] for e in p_new.iterdir() if e.suffix == ".txt"]

for e in p_old.iterdir():
    if e.suffix == ".txt":
        code = get_code(e.name) 
        if code in codes_new_ocr:
            compare_p = Path(f"sammenlikn-ocr/{code}/")
            compare_p.mkdir(parents=True, exist_ok=True)
            
            dest = compare_p / e.name
            dest.write_text(e.read_text())
            
            new_ocr = p_new / f"{code}.txt"
            dest = compare_p / new_ocr.name
            dest.write_text(new_ocr.read_text())



In [20]:
p = Path("ny-ocr-dikt-idetfri/alto")
pattern = r"_C?I?\d*.alto"
files = list(p.iterdir())
book_dirs = sorted(list(set([re.split(pattern, file.name)[0] for file in files])))

for book_dir in book_dirs:
    book_dir_path = p / book_dir
    book_dir_path.mkdir(parents=True, exist_ok=True)
    print("book_dir_path", book_dir_path)
    for i, file in enumerate(files):
        if file.name.startswith(book_dir_path.name) and not file.is_dir():
            print(f"file:{file}\n file.name:{file.name}")
            #file.rename(book_dir_path / file.name)


book_dir_path ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006081800003
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006081800003_0001.alto
 file.name:URN:NBN:no-nb_digibok_2006081800003_0001.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006081800003_0027.alto
 file.name:URN:NBN:no-nb_digibok_2006081800003_0027.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006081800003_0037.alto
 file.name:URN:NBN:no-nb_digibok_2006081800003_0037.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006081800003_0031.alto
 file.name:URN:NBN:no-nb_digibok_2006081800003_0031.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006081800003_0019.alto
 file.name:URN:NBN:no-nb_digibok_2006081800003_0019.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006081800003_0022.alto
 file.name:URN:NBN:no-nb_digibok_2006081800003_0022.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006081800003_0032.alto
 file.name:URN:NBN:no-nb_digibok_2006081800003_0032

file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006082400061_0055.alto
 file.name:URN:NBN:no-nb_digibok_2006082400061_0055.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006082400061_0056.alto
 file.name:URN:NBN:no-nb_digibok_2006082400061_0056.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006082400061_0079.alto
 file.name:URN:NBN:no-nb_digibok_2006082400061_0079.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006082400061_0030.alto
 file.name:URN:NBN:no-nb_digibok_2006082400061_0030.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006082400061_0127.alto
 file.name:URN:NBN:no-nb_digibok_2006082400061_0127.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006082400061_0137.alto
 file.name:URN:NBN:no-nb_digibok_2006082400061_0137.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006082400061_0109.alto
 file.name:URN:NBN:no-nb_digibok_2006082400061_0109.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006082400061_008

file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006111501016_0138.alto
 file.name:URN:NBN:no-nb_digibok_2006111501016_0138.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006111501016_0034.alto
 file.name:URN:NBN:no-nb_digibok_2006111501016_0034.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006111501016_0041.alto
 file.name:URN:NBN:no-nb_digibok_2006111501016_0041.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006111501016_0075.alto
 file.name:URN:NBN:no-nb_digibok_2006111501016_0075.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006111501016_0111.alto
 file.name:URN:NBN:no-nb_digibok_2006111501016_0111.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006111501016_0121.alto
 file.name:URN:NBN:no-nb_digibok_2006111501016_0121.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006111501016_0071.alto
 file.name:URN:NBN:no-nb_digibok_2006111501016_0071.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006111501016_009

file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006111600006_0557.alto
 file.name:URN:NBN:no-nb_digibok_2006111600006_0557.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006111600006_0457.alto
 file.name:URN:NBN:no-nb_digibok_2006111600006_0457.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006111600006_0248.alto
 file.name:URN:NBN:no-nb_digibok_2006111600006_0248.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006111600006_0020.alto
 file.name:URN:NBN:no-nb_digibok_2006111600006_0020.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006111600006_0348.alto
 file.name:URN:NBN:no-nb_digibok_2006111600006_0348.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006111600006_0256.alto
 file.name:URN:NBN:no-nb_digibok_2006111600006_0256.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006111600006_0070.alto
 file.name:URN:NBN:no-nb_digibok_2006111600006_0070.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006111600006_008

file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006112101006_0325.alto
 file.name:URN:NBN:no-nb_digibok_2006112101006_0325.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006112101006_0118.alto
 file.name:URN:NBN:no-nb_digibok_2006112101006_0118.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006112101006_0422.alto
 file.name:URN:NBN:no-nb_digibok_2006112101006_0422.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006112101006_0451.alto
 file.name:URN:NBN:no-nb_digibok_2006112101006_0451.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006112101006_0291.alto
 file.name:URN:NBN:no-nb_digibok_2006112101006_0291.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006112101006_0265.alto
 file.name:URN:NBN:no-nb_digibok_2006112101006_0265.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006112101006_0352.alto
 file.name:URN:NBN:no-nb_digibok_2006112101006_0352.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2006112101006_043

...

file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013031324043_0251.alto
 file.name:URN:NBN:no-nb_digibok_2013031324043_0251.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013031324043_0129.alto
 file.name:URN:NBN:no-nb_digibok_2013031324043_0129.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013031324043_0118.alto
 file.name:URN:NBN:no-nb_digibok_2013031324043_0118.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013031324043_0006.alto
 file.name:URN:NBN:no-nb_digibok_2013031324043_0006.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013031324043_0240.alto
 file.name:URN:NBN:no-nb_digibok_2013031324043_0240.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013031324043_0172.alto
 file.name:URN:NBN:no-nb_digibok_2013031324043_0172.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013031324043_0210.alto
 file.name:URN:NBN:no-nb_digibok_2013031324043_0210.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013031324043_012

file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013042608071_0007.alto
 file.name:URN:NBN:no-nb_digibok_2013042608071_0007.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013042608071_0035.alto
 file.name:URN:NBN:no-nb_digibok_2013042608071_0035.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013042608071_0015.alto
 file.name:URN:NBN:no-nb_digibok_2013042608071_0015.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013042608071_0046.alto
 file.name:URN:NBN:no-nb_digibok_2013042608071_0046.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013042608071_I3.alto
 file.name:URN:NBN:no-nb_digibok_2013042608071_I3.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013042608071_0028.alto
 file.name:URN:NBN:no-nb_digibok_2013042608071_0028.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013042608071_0036.alto
 file.name:URN:NBN:no-nb_digibok_2013042608071_0036.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013042608071_0016.al

file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013061708135_0013.alto
 file.name:URN:NBN:no-nb_digibok_2013061708135_0013.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013061708135_0002.alto
 file.name:URN:NBN:no-nb_digibok_2013061708135_0002.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013061708135_0035.alto
 file.name:URN:NBN:no-nb_digibok_2013061708135_0035.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013061708135_0049.alto
 file.name:URN:NBN:no-nb_digibok_2013061708135_0049.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013061708135_0041.alto
 file.name:URN:NBN:no-nb_digibok_2013061708135_0041.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013061708135_C3.alto
 file.name:URN:NBN:no-nb_digibok_2013061708135_C3.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013061708135_0025.alto
 file.name:URN:NBN:no-nb_digibok_2013061708135_0025.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013061708135_0004.al

file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013070108121_0027.alto
 file.name:URN:NBN:no-nb_digibok_2013070108121_0027.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013070108121_0045.alto
 file.name:URN:NBN:no-nb_digibok_2013070108121_0045.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013070108121_0011.alto
 file.name:URN:NBN:no-nb_digibok_2013070108121_0011.alto
book_dir_path ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013070308041
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013070308041_0052.alto
 file.name:URN:NBN:no-nb_digibok_2013070308041_0052.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013070308041_0064.alto
 file.name:URN:NBN:no-nb_digibok_2013070308041_0064.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013070308041_0010.alto
 file.name:URN:NBN:no-nb_digibok_2013070308041_0010.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013070308041_0001.alto
 file.name:URN:NBN:no-nb_digibok_2013070308041_0001

file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013080508339_0016.alto
 file.name:URN:NBN:no-nb_digibok_2013080508339_0016.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013080508339_0045.alto
 file.name:URN:NBN:no-nb_digibok_2013080508339_0045.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013080508339_0033.alto
 file.name:URN:NBN:no-nb_digibok_2013080508339_0033.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013080508339_0064.alto
 file.name:URN:NBN:no-nb_digibok_2013080508339_0064.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013080508339_0090.alto
 file.name:URN:NBN:no-nb_digibok_2013080508339_0090.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013080508339_0102.alto
 file.name:URN:NBN:no-nb_digibok_2013080508339_0102.alto
file:ny-ocr-dikt-idetfri/alto/URN:NBN:no-nb_digibok_2013080508339_0009.alto
 file.name:URN:NBN:no-nb_digibok_2013080508339_0009.alto
